<div style="color:blue"><b>This notebook reads the metadata control table for given entity and parses all the relevant fields listed in the contorl table</b></div>

- > This a generic notebook for all component entities and can be reused based on parameters provided

- > Need to modify above paramters accoding to the entity being processed

1. **Setting up parameters**

In [0]:
# Catalog & Schema Setup
dbutils.widgets.text("Catalog_Name", "racd_dev")
dbutils.widgets.text("Schema_Name", "shared")
catalogName=dbutils.widgets.get("Catalog_Name")
schemaName=dbutils.widgets.get("Schema_Name")

# File Name Setup
dbutils.widgets.text("File_Name", "EPIC%.xml")
fileName=dbutils.widgets.get("File_Name")

# Entity Parameter
dbutils.widgets.text("Entity_Name", "Patient")
entityName=dbutils.widgets.get("Entity_Name")

# Component Parameter
dbutils.widgets.text("Component_Name", "Results")
compName=dbutils.widgets.get("Component_Name")

# Source Parameters
dbutils.widgets.text("Source_Name", "CCDA")
sourceName=dbutils.widgets.get("Source_Name")
dbutils.widgets.text("Source_Type", "File")
sourceType=dbutils.widgets.get("Source_Type")

print(catalogName)
print(schemaName)
print(fileName)
print(entityName)
print(compName)
print(sourceName)





racd_dev
shared
HIXNY%.xml
ENCOUNTER
Encounters
CCDA


2. **Reading Metadata Mapping Table**

In [0]:
df_elements=spark.read.table("dev_teams.racd.source_mappings_ccda_1").filter("Source_Entity_Name='"+fileName+"' AND Target_Entity_Name='"+entityName+"' AND Active_Indicator='Y'")
df_elements_all=spark.read.table("dev_teams.racd.source_mappings_ccda_1").filter("Source_Entity_Name='"+fileName+"'")

display(df_elements)

Source_System Source_Entity_Type Source_Entity_Name Element_Type Section_Name Section_Path Section_Type Section_Level Section_keys Parent_Section_Name Column_Name Column_Path Target_Entity_Name Active_Indicator CCDA File HIXNY%.xml Section EncountersEntry $.section.entry Array 0 null EncountersEntry null null ENCOUNTER Y CCDA File HIXNY%.xml Section Encounter $.encounter Struct 1 ENCOUNTER_ID EncountersEntry null null ENCOUNTER Y CCDA File HIXNY%.xml Column Encounter null null null null null ENCOUNTER_ID $.id._extension ENCOUNTER Y CCDA File HIXNY%.xml Column Encounter null null null null null ENCOUNTER_CODE $.code._code ENCOUNTER Y CCDA File HIXNY%.xml Column Encounter null null null null null ENCOUNTER_TEXT $.code.originalText.reference.value ENCOUNTER Y CCDA File HIXNY%.xml Column Encounter null null null null null ENCOUNTER_START_TIME $.effectiveTime.low._value ENCOUNTER Y CCDA File HIXNY%.xml Column Encounter null null null null null ENCOUNTER_END_TIME $.effectiveTime.high._value ENCOUNTER Y CCDA File HIXNY%.xml Section EncounterParticipant $.participant Struct 2 null Encounter null null ENCOUNTER Y CCDA File HIXNY%.xml Column EncounterParticipant null null null null null PARTICIPANT_TYPE_CODE $.typeCode ENCOUNTER Y CCDA File HIXNY%.xml Column EncounterParticipant null null null null null PARTICIPANT_ID $.participantRole.id._extension ENCOUNTER Y CCDA File HIXNY%.xml Column EncounterParticipant null null null null null PARTICIPANT_CODE $.participantRole.code._code ENCOUNTER Y CCDA File HIXNY%.xml Column EncounterParticipant null null null null null PARTICIPANT_CODE_SYSTEM_NAME $.participantRole.code._codeSystemName ENCOUNTER Y CCDA File HIXNY%.xml Column EncounterParticipant null null null null null PARTICIPANT_CODE_DISPLAY_NAME $.participantRole.code._displayName ENCOUNTER Y

**Section List**

In [0]:
from pyspark.sql.functions import row_number, concat

dict_section={row["Section_Name"]:row["Section_Path"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
dict_section_reg={row["Section_Name"]: row["Section_Path"] for row in df_elements.filter(df_elements.Element_Type == 'Section').collect() if row["Section_Type"] == 'Struct'}
dict_section_arr={row["Section_Name"]: row["Section_Path"] for row in df_elements.filter(df_elements.Element_Type == 'Section').collect() if row["Section_Type"] == 'Array'}

#dict_section_path = {index: (row["Section_Name"], row["Section_Path"]) for index, row in enumerate(df_elements.filter(df_elements.Element_Type == 'Section').collect())}

print("All Sections are : ",dict_section)
print("Regualr Sections are : ",dict_section_reg)
print("Array Sections are : ",dict_section_arr)

All Sections are :  {'Document': '', 'Components': '$.component.structuredBody.component', 'EncountersEntry': '$.section.entry', 'Encounter': '$.encounter', 'EncounterParticipant': '$.participant', 'ObservationEntry': '$.section.entry', 'ObservationOrganizer': '$.organizer', 'ObservationComponent': '$.component', 'Observation': '$.observation', 'patientRole': '$.recordTarget.patientRole', 'patient': '$.patient', 'patientAddr': '$.addr', 'patientTelecom': '$.telecom'}
Regualr Sections are :  {'Encounter': '$.encounter', 'EncounterParticipant': '$.participant'}
Array Sections are :  {'EncountersEntry': '$.section.entry'}


**Columns List**

In [0]:
Columns=[{'Section': row["Section_Name"], 'Column_Name': row["Column_Name"], 'Column_Path': row["Column_Path"]} for row in df_elements.filter(df_elements.Element_Type == 'Column').collect() ]
display(Columns)


Column_Name Column_Path Section ENCOUNTER_ID $.id._extension Encounter ENCOUNTER_CODE $.code._code Encounter ENCOUNTER_TEXT $.code.originalText.reference.value Encounter ENCOUNTER_START_TIME $.effectiveTime.low._value Encounter ENCOUNTER_END_TIME $.effectiveTime.high._value Encounter PARTICIPANT_TYPE_CODE $.typeCode EncounterParticipant PARTICIPANT_ID $.participantRole.id._extension EncounterParticipant PARTICIPANT_CODE $.participantRole.code._code EncounterParticipant PARTICIPANT_CODE_SYSTEM_NAME $.participantRole.code._codeSystemName EncounterParticipant PARTICIPANT_CODE_DISPLAY_NAME $.participantRole.code._displayName EncounterParticipant

3. **Reading the variant data from provided file(s)**

In [0]:
from pyspark.sql.functions import variant_get,row_number

#Reading Variant field data
df=spark.sql("select MEDICAL_RECORD_FILENAME,CCDA_RAW from `" + catalogName + "`.`" + schemaName + "`.brnz_ccda_raw_variant WHERE MEDICAL_RECORD_FILENAME like '%" + fileName + "%' ")

#Appending Docuemnt ID as key 
df_file_elements=spark.read.table("dev_teams.racd.source_mappings_ccda_1").filter("Source_Entity_Name='"+fileName+"' AND Column_Name='Document_ID'")
doc_id_path={row["Column_Name"]:row["Column_Path"] for row in df_file_elements.filter( (df_file_elements.Section_Name == 'Document')).collect()} 

from pyspark.sql.functions import col
df=df.withColumn("Document_ID",variant_get(df.CCDA_RAW,doc_id_path["Document_ID"],"string")).filter(col('Document_ID')=='3b7d532f-a064-41b3-8de7-2337bf865f93')


display(df)

MEDICAL_RECORD_FILENAME CCDA_RAW Document_ID HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml {"_xmlns":"urn:hl7-org:v3","author":{"_typeCode":"AUT","assignedAuthor":{"_classCode":"ASSIGNED","addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"assignedAuthoringDevice":{"manufacturerModelName":"InterSystems","softwareName":"InterSystems HealthShare"},"id":{"_root":"2.16.840.1.113883.3.86.3"},"representedOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"DECOMMISSIONED-HIXNY","telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}},"telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}},"templateId":{"_root":"2.16.840.1.113883.10.20.22.4.119"},"time":{"_value":"20251115011002-0500"}},"code":{"_code":"34133-9","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LN","_displayName":"Summarization of Episode Note"},"component":{"structuredBody":{"component":[{"section":{"code":{"_code":"48765-2","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LN","_displayName":"Allergies, Adverse Reactions, Alerts"},"entry":{"_typeCode":"DRIV","act":{"_classCode":"ACT","_moodCode":"EVN","code":{"_code":"CONC","_codeSystem":"2.16.840.1.113883.5.6","_codeSystemName":"ActClass","_displayName":"Concern"},"effectiveTime":{"low":{"_nullFlavor":"NA"}},"entryRelationship":{"_inversionInd":false,"_typeCode":"SUBJ","observation":{"_classCode":"OBS","_moodCode":"EVN","_negationInd":true,"code":{"_code":"ASSERTION","_codeSystem":"2.16.840.1.113883.5.4","_codeSystemName":"HL7"},"effectiveTime":{"low":{"_nullFlavor":"NA"}},"id":{"_nullFlavor":"NI"},"participant":{"_typeCode":"CSM","participantRole":{"_classCode":"MANU","playingEntity":{"_classCode":"MMAT","code":{"_nullFlavor":"NA"}}}},"statusCode":{"_code":"completed"},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.7"},{"_extension":"2014-06-09","_root":"2.16.840.1.113883.10.20.22.4.7"}],"value":{"_code":419199007,"_codeSystem":"2.16.840.1.113883.6.96","_codeSystemName":"SNOMEDCT","_displayName":"Allergy to substance (disorder)","_xmlns:xsi":"http://www.w3.org/2001/XMLSchema-instance","_xsi:type":"CD"}}},"id":{"_nullFlavor":"UNK"},"statusCode":{"_code":"active"},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.30"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.30"}]}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.2.6.1"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.2.6.1"}],"text":"This patient has no known allergies or adverse reactions.","title":"Allergies, Adverse Reactions, Alerts"}},{"section":{"_nullFlavor":"NI","code":{"_code":"10160-0","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LN","_displayName":"History of Medication Use"},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.2.1.1"},{"_extension":"2014-06-09","_root":"2.16.840.1.113883.10.20.22.2.1.1"}],"text":"This patient has no known medications.","title":"Medications"}},{"section":{"code":{"_code":"11450-4","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LN","_displayName":"Problem list"},"entry":{"_typeCode":"DRIV","act":{"_classCode":"ACT","_moodCode":"EVN","code":{"_code":"CONC","_codeSystem":"2.16.840.1.113883.5.6","_codeSystemName":"ActClass","_displayName":"Concern"},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_nullFlavor":"UNK"}},"entryRelationship":{"_typeCode":"SUBJ","observation":{"_classCode":"OBS","_moodCode":"EVN","_negationInd":true,"code":{"_code":55607006,"_codeSystem":"2.16.840.1.113883.6.96","_codeSystemName":"SNOMED-CT","_displayName":"Problem","translation":{"_code":"75326-9","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LOINC","_displayName":"Problem"}},"effectiveTime":{"low":{"_nullFlavor":"NA"}},"id":{"_nullFlavor":"NI"},"statusCode":{"_

4. **Extracting and exploding components section**

In [0]:
%skip
from pyspark.sql.functions import * 

Section_Name='Components'

df_components=df.select("MEDICAL_RECORD_FILENAME","Document_ID",variant_get(df.CCDA_RAW,dict_section[Section_Name],"variant").alias('Components'))

df_components_expld=df_components.lateralJoin(spark.tvf.variant_explode('Components'))



In [0]:
from pyspark.sql.functions import *

Section_Name = 'Components'

# Step 1: Build the components df
df_components = df.select(
    "MEDICAL_RECORD_FILENAME",
    "Document_ID",
    variant_get(df.CCDA_RAW, dict_section[Section_Name], "variant").alias('Components')
)

# Step 2: Register as temp view
df_components.createOrReplaceTempView("df_components_view")

# Step 3: Use SQL LATERAL with variant_explode
df_components_expld = spark.sql("""
    SELECT 
        MEDICAL_RECORD_FILENAME,
        Document_ID,
        pos,
        value
    FROM df_components_view,
    LATERAL variant_explode(Components)
""")

display(df_components_expld)

MEDICAL_RECORD_FILENAME Document_ID pos value HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 0 {"section":{"code":{"_code":"48765-2","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LN","_displayName":"Allergies, Adverse Reactions, Alerts"},"entry":{"_typeCode":"DRIV","act":{"_classCode":"ACT","_moodCode":"EVN","code":{"_code":"CONC","_codeSystem":"2.16.840.1.113883.5.6","_codeSystemName":"ActClass","_displayName":"Concern"},"effectiveTime":{"low":{"_nullFlavor":"NA"}},"entryRelationship":{"_inversionInd":false,"_typeCode":"SUBJ","observation":{"_classCode":"OBS","_moodCode":"EVN","_negationInd":true,"code":{"_code":"ASSERTION","_codeSystem":"2.16.840.1.113883.5.4","_codeSystemName":"HL7"},"effectiveTime":{"low":{"_nullFlavor":"NA"}},"id":{"_nullFlavor":"NI"},"participant":{"_typeCode":"CSM","participantRole":{"_classCode":"MANU","playingEntity":{"_classCode":"MMAT","code":{"_nullFlavor":"NA"}}}},"statusCode":{"_code":"completed"},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.7"},{"_extension":"2014-06-09","_root":"2.16.840.1.113883.10.20.22.4.7"}],"value":{"_code":419199007,"_codeSystem":"2.16.840.1.113883.6.96","_codeSystemName":"SNOMEDCT","_displayName":"Allergy to substance (disorder)","_xmlns:xsi":"http://www.w3.org/2001/XMLSchema-instance","_xsi:type":"CD"}}},"id":{"_nullFlavor":"UNK"},"statusCode":{"_code":"active"},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.30"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.30"}]}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.2.6.1"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.2.6.1"}],"text":"This patient has no known allergies or adverse reactions.","title":"Allergies, Adverse Reactions, Alerts"}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 1 {"section":{"_nullFlavor":"NI","code":{"_code":"10160-0","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LN","_displayName":"History of Medication Use"},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.2.1.1"},{"_extension":"2014-06-09","_root":"2.16.840.1.113883.10.20.22.2.1.1"}],"text":"This patient has no known medications.","title":"Medications"}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 2 {"section":{"code":{"_code":"11450-4","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LN","_displayName":"Problem list"},"entry":{"_typeCode":"DRIV","act":{"_classCode":"ACT","_moodCode":"EVN","code":{"_code":"CONC","_codeSystem":"2.16.840.1.113883.5.6","_codeSystemName":"ActClass","_displayName":"Concern"},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_nullFlavor":"UNK"}},"entryRelationship":{"_typeCode":"SUBJ","observation":{"_classCode":"OBS","_moodCode":"EVN","_negationInd":true,"code":{"_code":55607006,"_codeSystem":"2.16.840.1.113883.6.96","_codeSystemName":"SNOMED-CT","_displayName":"Problem","translation":{"_code":"75326-9","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LOINC","_displayName":"Problem"}},"effectiveTime":{"low":{"_nullFlavor":"NA"}},"id":{"_nullFlavor":"NI"},"statusCode":{"_code":"completed"},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.4"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.4"}],"value":{"_code":55607006,"_codeSystem":"2.16.840.1.113883.6.96","_codeSystemName":"SNOMEDCT","_displayName":"Problem","_xmlns:xsi":"http://www.w3.org/2001/XMLSchema-instance","_xsi:type":"CD","originalText":null}}},"id":{"_nullFlavor":"UNK"},"statusCode":{"_code":"completed"},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.3"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.3"}]}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.2.5.1"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.2.5.1"}],"text":"This patient has no known problems.","title":"Problems"}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 

In [0]:
%skip

display(df_components_expld)

**Filtering provided component from exploded components list**

In [0]:
df_components_items={}
df_components_items[compName]=df_components_expld.filter(variant_get('value','$.section.title',"string")==compName)

display(df_components_items[compName])

MEDICAL_RECORD_FILENAME Document_ID pos value HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 6 {"section":{"code":{"_code":"46240-8","_codeSystem":"2.16.840.1.113883.6.1","_codeSystemName":"LN","_displayName":"History of Encounters"},"entry":[{"encounter":{"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-1"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20240415063825}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":34611941,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}}},"id":[{"_root":"2.16.840.1.113883.3.241.2.1"},{"_displayable":true,"_extension":"ADIR01","_root":"2.16.840.1.113883.4.319"}],"name":"Glens Falls Hospital","telecom":{"_nullFlavor":"UNK"}},"telecom":{"_nullFlavor":"UNK"}}},"participant":{"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.49"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.49"}],"text":{"reference":{"_value":"#encounterNarrative-1"}}}},{"encounter":{"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-2"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20221213054920}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":33860921,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":

4. **Looping through each section listed out in contorl table and parsing out the fields required**

In [0]:
%skip
import pyspark.sql.functions as F
from pyspark.sql.functions import *

# Initializing Array Sections Dataframe Dictionary
df_sections_arr={}
df_section_elements={}

df_elements=spark.read.table("dev_teams.racd.source_mappings_ccda_1").filter("Source_Entity_Name='"+fileName+"' AND Target_Entity_Name='"+entityName+"'")

#Section Levels
dict_level={row["Section_Level"]:row["Section_Name"] for row in df_elements.filter(df_elements.Element_Type == 'Section').collect()}
print("Section Levels:",dict_level)

#parent sections
dict_parent={row["Section_Name"]:row["Parent_Section_Name"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
print("Parent Sections:",dict_parent)

#Section Data Types
dict_types={row["Section_Name"]:row["Section_Type"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
print("Section Data Types:",dict_types)

#Section Paths
dict_path={row["Section_Name"]:row["Section_Path"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
print("Section Paths:",dict_path)

#Section Keys
dict_keys={row["Section_Name"]:row["Section_keys"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
print("Section Keys:",dict_keys)


#Looping through each section of given entity based on Array or Struct types

#Loop Through based on levels
for a in dict_level:
    print("Section Priority Order: ",a)
    
    #Loop Through each section of given level
    for i in [dict_level[a]]:
        print("Section being processed is:",i)
        print("Section Type:",dict_types[i])
        
        #Top Section: Reading respective component
        if a==0:
            df_sections_arr[f'df_section_{i}'] = df_components_items[compName].select("MEDICAL_RECORD_FILENAME","Document_ID",variant_get("value",dict_path[dict_level[a]],"variant").alias(f'{i}'))
            display(df_sections_arr[f'df_section_{i}'])

            #Exploding array section to get individual rows
            #replace the below line with new code
            #df_sections_arr[f'df_section_{i}_expld']=df_sections_arr[f'df_section_{i}'].lateralJoin(spark.tvf.variant_explode(f'{i}').alias(f'{i}'))

        for i in dict_section.keys():
            # Register current section df as temp view
            df_sections_arr[f'df_section_{i}'].createOrReplaceTempView(f"df_section_{i}_view")
            
            # Use SQL LATERAL instead of lateralJoin
            df_sections_arr[f'df_section_{i}_expld'] = spark.sql(f"""
                SELECT 
                    MEDICAL_RECORD_FILENAME,
                    Document_ID,
                    pos,
                    value
                FROM df_section_{i}_view,
                LATERAL variant_explode(`{i}`)
            """)
            print("Section Entries Exploded:")
            display(df_sections_arr[f'df_section_{i}_expld'])

        #Rest of Sections
        else:
            print("section being processed:",f'df_section_{i}')
            print("Section Path:",dict_path[dict_level[a]])
            print("Section Type:",dict_types[i])
            parentSection=dict_parent[i]
            print("parent section:",parentSection)
            parentKeys=dict_keys[parentSection]
            print("Parent Keys:",parentKeys)
            
            #Parent Section is Array
            if dict_types[parentSection]=='Array':
                
                    #Child Section being processed is Struct
                    if dict_types[i]=='Struct':
                        print("Parent is Array & Child is String:")

                        #Reading parent section as exploded
                        df_sections_arr[f'df_section_{i}'] =df_sections_arr[f'df_section_{parentSection}_expld'].select("MEDICAL_RECORD_FILENAME","Document_ID",variant_get("value",dict_path[dict_level[a]],"variant").alias(f'{i}'))
                        #Filtering 
                        df_sections_arr[f'df_section_{i}']=df_sections_arr[f'df_section_{i}'].filter(df_sections_arr[f'df_section_{i}'][f'{i}'].isNotNull())
                        
                        display(df_sections_arr[f'df_section_{i}'])

                        #Fetching Columns
                        df_section_elements[f'{i}']=df_sections_arr[f'df_section_{i}']

                        #Looping through each column in the mapping table column list for processing section
                        for c in [col for col in Columns if col['Section']==i]:
                            df_section_elements[f'{i}']=df_section_elements[f'{i}'].withColumn(c['Column_Name'],variant_get(f'{i}', c['Column_Path'], "string"))
                            
                        display(df_section_elements[f'{i}'])

                    #Child Section being processed is Array
                    else:
                        print("Parent is Array & Child is Array:")

                        #Reading parent section as exploded
                        df_sections_arr[f'df_section_{i}'] =df_sections_arr[f'df_section_{parentSection}_expld'].select("MEDICAL_RECORD_FILENAME","Document_ID",variant_get("value",dict_path[dict_level[a]],"variant").alias(f'{i}'))
                        
                        #Exploding child array section to get individual rows
                        df_sections_arr[f'df_section_{i}_expld']=df_sections_arr[f'df_section_{i}'].lateralJoin(spark.tvf.variant_explode(f'{i}').alias(f'{i}'))
                        df_sections_arr[f'df_section_{i}_expld']=df_sections_arr[f'df_section_{i}_expld'].filter(df_sections_arr[f'df_section_{i}'][f'{i}'].isNotNull())
                        
                        display(df_sections_arr[f'df_section_{i}_expld'])

                        #Fetching Columns
                        df_section_elements[f'{i}']=df_sections_arr[f'df_section_{i}_expld']

                        #Looping through each column in the mapping table column list for processing section
                        for c in [col for col in Columns if col['Section']==i]:
                            df_section_elements[f'{i}']=df_section_elements[f'{i}'].withColumn(c['Column_Name'],variant_get(f'{i}', c['Column_Path'], "string"))
                            
                        display(df_section_elements[f'{i}'])
            
            #Parent Section is Struct
            else:
                    #Child Section being processed is Struct
                    if dict_types[i]=='Struct':

                        print("Parent is Struct & Child is Struct:")

                        #Reading parent section 
                        df_sections_arr[f'df_section_{i}'] =df_section_elements[f'{parentSection}'].select("MEDICAL_RECORD_FILENAME","Document_ID",F.col(parentKeys),variant_get(dict_parent[i],dict_path[dict_level[a]],"variant").alias(f'{i}'))
                        df_sections_arr[f'df_section_{i}']=df_sections_arr[f'df_section_{i}'].filter(df_sections_arr[f'df_section_{i}'][f'{i}'].isNotNull())
                        
                        display(df_sections_arr[f'df_section_{i}'])

                         #Fetching Columns
                        df_section_elements[f'{i}']=df_sections_arr[f'df_section_{i}']

                        #Looping through each column in the mapping table column list for processing section
                        for c in [col for col in Columns if col['Section']==i]:
                            df_section_elements[f'{i}']=df_section_elements[f'{i}'].withColumn(c['Column_Name'],variant_get(f'{i}', c['Column_Path'], "string"))
                            
                        display(df_section_elements[f'{i}'])


                    else:
                        print("Parent is Struct & Child is Array:")

                        #Reading parent section
                        df_sections_arr[f'df_section_{i}'] =df_section_elements[f'{parentSection}'].select("MEDICAL_RECORD_FILENAME","Document_ID",F.col(parentKeys),variant_get(dict_parent[i],dict_path[dict_level[a]],"variant").alias(f'{i}'))

                        #Exploding child array section to get individual rows
                        df_sections_arr[f'df_section_{i}_expld']=df_sections_arr[f'df_section_{i}'].lateralJoin(spark.tvf.variant_explode(f'{i}').alias(f'{i}'))
                        df_sections_arr[f'df_section_{i}_expld']=df_sections_arr[f'df_section_{i}_expld'].filter(df_sections_arr[f'df_section_{i}'][f'{i}'].isNotNull())
                       
                        display(df_sections_arr[f'df_section_{i}_expld'])

                         #Fetching Columns
                        df_section_elements[f'{i}']=df_sections_arr[f'df_section_{i}_expld']
                        
                        #Looping through each column in the mapping table column list for processing section
                        for c in [col for col in Columns if col['Section']==i]:
                            df_section_elements[f'{i}']=df_section_elements[f'{i}'].withColumn(c['Column_Name'],variant_get(f'{i}', c['Column_Path'], "string"))
                            
                        display(df_section_elements[f'{i}'])


In [0]:
import pyspark.sql.functions as F
from pyspark.sql.functions import *

# Helper function to replace lateralJoin
def lateral_variant_explode(df, section_name):
    df.createOrReplaceTempView(f"_temp_lateral_view")
    return spark.sql(f"""
        SELECT 
            MEDICAL_RECORD_FILENAME,
            Document_ID,
            pos,
            value
        FROM _temp_lateral_view,
        LATERAL variant_explode(`{section_name}`)
    """)

# Helper function for lateral explode when parent keys are needed
def lateral_variant_explode_with_keys(df, section_name, parent_keys):
    df.createOrReplaceTempView(f"_temp_lateral_view")
    return spark.sql(f"""
        SELECT 
            MEDICAL_RECORD_FILENAME,
            Document_ID,
            {parent_keys},
            pos,
            value
        FROM _temp_lateral_view,
        LATERAL variant_explode(`{section_name}`)
    """)

# Initializing Array Sections Dataframe Dictionary
df_sections_arr = {}
df_section_elements = {}

df_elements = spark.read.table("dev_teams.racd.source_mappings_ccda_1").filter("Source_Entity_Name='"+fileName+"' AND Target_Entity_Name='"+entityName+"'")

# Section Levels
dict_level = {row["Section_Level"]:row["Section_Name"] for row in df_elements.filter(df_elements.Element_Type == 'Section').collect()}
print("Section Levels:", dict_level)

# Parent Sections
dict_parent = {row["Section_Name"]:row["Parent_Section_Name"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
print("Parent Sections:", dict_parent)

# Section Data Types
dict_types = {row["Section_Name"]:row["Section_Type"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
print("Section Data Types:", dict_types)

# Section Paths
dict_path = {row["Section_Name"]:row["Section_Path"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
print("Section Paths:", dict_path)

# Section Keys
dict_keys = {row["Section_Name"]:row["Section_keys"] for row in df_elements_all.filter(df_elements_all.Element_Type == 'Section').collect()}
print("Section Keys:", dict_keys)


# Loop Through based on levels
for a in dict_level:
    print("Section Priority Order:", a)

    # Loop Through each section of given level
    for i in [dict_level[a]]:
        print("Section being processed is:", i)
        print("Section Type:", dict_types[i])

        # ── Top Section ──────────────────────────────────────────────────────
        if a == 0:
            df_sections_arr[f'df_section_{i}'] = df_components_items[compName].select(
                "MEDICAL_RECORD_FILENAME",
                "Document_ID",
                variant_get("value", dict_path[dict_level[a]], "variant").alias(f'{i}')
            )
            display(df_sections_arr[f'df_section_{i}'])

            # FIX 1: Removed the wrong inner loop that was overwriting i
            # FIX 2: Replaced lateralJoin with helper function
            df_sections_arr[f'df_section_{i}_expld'] = lateral_variant_explode(
                df_sections_arr[f'df_section_{i}'], i
            )
            print("Section Entries Exploded:")
            display(df_sections_arr[f'df_section_{i}_expld'])

        # ── Rest of Sections ─────────────────────────────────────────────────
        else:
            print("Section being processed:", f'df_section_{i}')
            print("Section Path:", dict_path[dict_level[a]])
            print("Section Type:", dict_types[i])
            parentSection = dict_parent[i]
            print("Parent section:", parentSection)
            parentKeys = dict_keys[parentSection]
            print("Parent Keys:", parentKeys)

            # Parent Section is Array
            if dict_types[parentSection] == 'Array':

                # Child is Struct
                if dict_types[i] == 'Struct':
                    print("Parent is Array & Child is Struct:")

                    df_sections_arr[f'df_section_{i}'] = df_sections_arr[f'df_section_{parentSection}_expld'].select(
                        "MEDICAL_RECORD_FILENAME",
                        "Document_ID",
                        variant_get("value", dict_path[dict_level[a]], "variant").alias(f'{i}')
                    )
                    df_sections_arr[f'df_section_{i}'] = df_sections_arr[f'df_section_{i}'].filter(
                        df_sections_arr[f'df_section_{i}'][f'{i}'].isNotNull()
                    )
                    display(df_sections_arr[f'df_section_{i}'])

                    df_section_elements[f'{i}'] = df_sections_arr[f'df_section_{i}']
                    for c in [col for col in Columns if col['Section'] == i]:
                        df_section_elements[f'{i}'] = df_section_elements[f'{i}'].withColumn(
                            c['Column_Name'], variant_get(f'{i}', c['Column_Path'], "string")
                        )
                    display(df_section_elements[f'{i}'])

                # Child is Array
                else:
                    print("Parent is Array & Child is Array:")

                    df_sections_arr[f'df_section_{i}'] = df_sections_arr[f'df_section_{parentSection}_expld'].select(
                        "MEDICAL_RECORD_FILENAME",
                        "Document_ID",
                        variant_get("value", dict_path[dict_level[a]], "variant").alias(f'{i}')
                    )

                    # FIX 3: Replaced lateralJoin with helper function
                    df_sections_arr[f'df_section_{i}_expld'] = lateral_variant_explode(
                        df_sections_arr[f'df_section_{i}'], i
                    )
                    df_sections_arr[f'df_section_{i}_expld'] = df_sections_arr[f'df_section_{i}_expld'].filter(
                        df_sections_arr[f'df_section_{i}_expld']['value'].isNotNull()
                    )
                    display(df_sections_arr[f'df_section_{i}_expld'])

                    df_section_elements[f'{i}'] = df_sections_arr[f'df_section_{i}_expld']
                    for c in [col for col in Columns if col['Section'] == i]:
                        df_section_elements[f'{i}'] = df_section_elements[f'{i}'].withColumn(
                            c['Column_Name'], variant_get(f'{i}', c['Column_Path'], "string")
                        )
                    display(df_section_elements[f'{i}'])

            # Parent Section is Struct
            else:

                # Child is Struct
                if dict_types[i] == 'Struct':
                    print("Parent is Struct & Child is Struct:")

                    df_sections_arr[f'df_section_{i}'] = df_section_elements[f'{parentSection}'].select(
                        "MEDICAL_RECORD_FILENAME",
                        "Document_ID",
                        F.col(parentKeys),
                        variant_get(dict_parent[i], dict_path[dict_level[a]], "variant").alias(f'{i}')
                    )
                    df_sections_arr[f'df_section_{i}'] = df_sections_arr[f'df_section_{i}'].filter(
                        df_sections_arr[f'df_section_{i}'][f'{i}'].isNotNull()
                    )
                    display(df_sections_arr[f'df_section_{i}'])

                    df_section_elements[f'{i}'] = df_sections_arr[f'df_section_{i}']
                    for c in [col for col in Columns if col['Section'] == i]:
                        df_section_elements[f'{i}'] = df_section_elements[f'{i}'].withColumn(
                            c['Column_Name'], variant_get(f'{i}', c['Column_Path'], "string")
                        )
                    display(df_section_elements[f'{i}'])

                # Child is Array
                else:
                    print("Parent is Struct & Child is Array:")

                    df_sections_arr[f'df_section_{i}'] = df_section_elements[f'{parentSection}'].select(
                        "MEDICAL_RECORD_FILENAME",
                        "Document_ID",
                        F.col(parentKeys),
                        variant_get(dict_parent[i], dict_path[dict_level[a]], "variant").alias(f'{i}')
                    )

                    # FIX 4: Replaced lateralJoin with helper function (preserving parentKeys)
                    df_sections_arr[f'df_section_{i}_expld'] = lateral_variant_explode_with_keys(
                        df_sections_arr[f'df_section_{i}'], i, parentKeys
                    )
                    df_sections_arr[f'df_section_{i}_expld'] = df_sections_arr[f'df_section_{i}_expld'].filter(
                        df_sections_arr[f'df_section_{i}_expld']['value'].isNotNull()
                    )
                    display(df_sections_arr[f'df_section_{i}_expld'])

                    df_section_elements[f'{i}'] = df_sections_arr[f'df_section_{i}_expld']
                    for c in [col for col in Columns if col['Section'] == i]:
                        df_section_elements[f'{i}'] = df_section_elements[f'{i}'].withColumn(
                            c['Column_Name'], variant_get(f'{i}', c['Column_Path'], "string")
                        )
                    display(df_section_elements[f'{i}'])

Section Levels: {0: 'EncountersEntry', 1: 'Encounter', 2: 'EncounterParticipant'}
Parent Sections: {'Document': '', 'Components': '', 'EncountersEntry': 'EncountersEntry', 'Encounter': 'EncountersEntry', 'EncounterParticipant': 'Encounter', 'ObservationEntry': 'ObservationEntry', 'ObservationOrganizer': 'ObservationEntry', 'ObservationComponent': 'ObservationOrganizer', 'Observation': 'ObservationComponent', 'patientRole': 'patientRole', 'patient': 'patientRole', 'patientAddr': 'patientRole', 'patientTelecom': 'patientRole'}
Section Data Types: {'Document': '', 'Components': 'Array', 'EncountersEntry': 'Array', 'Encounter': 'Struct', 'EncounterParticipant': 'Struct', 'ObservationEntry': 'Array', 'ObservationOrganizer': 'Struct', 'ObservationComponent': 'Array', 'Observation': 'Struct', 'patientRole': 'Struct', 'patient': 'Struct', 'patientAddr': 'Array', 'patientTelecom': 'Array'}
Section Paths: {'Document': '', 'Components': '$.component.structuredBody.component', 'EncountersEntry': '

MEDICAL_RECORD_FILENAME Document_ID EncountersEntry HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 [{"encounter":{"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-1"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20240415063825}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":34611941,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}}},"id":[{"_root":"2.16.840.1.113883.3.241.2.1"},{"_displayable":true,"_extension":"ADIR01","_root":"2.16.840.1.113883.4.319"}],"name":"Glens Falls Hospital","telecom":{"_nullFlavor":"UNK"}},"telecom":{"_nullFlavor":"UNK"}}},"participant":{"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.49"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.49"}],"text":{"reference":{"_value":"#encounterNarrative-1"}}}},{"encounter":{"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-2"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20221213054920}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":33860921,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}}},"id":[{"_root":"2.16.840.1.113883.3.241.2.1"},{"

Section Entries Exploded:


MEDICAL_RECORD_FILENAME Document_ID pos value HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 0 {"encounter":{"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-1"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20240415063825}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":34611941,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}}},"id":[{"_root":"2.16.840.1.113883.3.241.2.1"},{"_displayable":true,"_extension":"ADIR01","_root":"2.16.840.1.113883.4.319"}],"name":"Glens Falls Hospital","telecom":{"_nullFlavor":"UNK"}},"telecom":{"_nullFlavor":"UNK"}}},"participant":{"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.49"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.49"}],"text":{"reference":{"_value":"#encounterNarrative-1"}}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 1 {"encounter":{"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-2"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20221213054920}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":33860921,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom"

Section Priority Order: 1
Section being processed is: Encounter
Section Type: Struct
Section being processed: df_section_Encounter
Section Path: $.encounter
Section Type: Struct
Parent section: EncountersEntry
Parent Keys: None
Parent is Array & Child is Struct:


MEDICAL_RECORD_FILENAME Document_ID Encounter HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 {"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-1"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20240415063825}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":34611941,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}}},"id":[{"_root":"2.16.840.1.113883.3.241.2.1"},{"_displayable":true,"_extension":"ADIR01","_root":"2.16.840.1.113883.4.319"}],"name":"Glens Falls Hospital","telecom":{"_nullFlavor":"UNK"}},"telecom":{"_nullFlavor":"UNK"}}},"participant":{"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.49"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.49"}],"text":{"reference":{"_value":"#encounterNarrative-1"}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 {"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-2"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20221213054920}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":33860921,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom":{"_use":"WP","_value":"tel:(51

MEDICAL_RECORD_FILENAME Document_ID Encounter ENCOUNTER_ID ENCOUNTER_CODE ENCOUNTER_TEXT ENCOUNTER_START_TIME ENCOUNTER_END_TIME HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 {"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-1"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20240415063825}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":34611941,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}}},"id":[{"_root":"2.16.840.1.113883.3.241.2.1"},{"_displayable":true,"_extension":"ADIR01","_root":"2.16.840.1.113883.4.319"}],"name":"Glens Falls Hospital","telecom":{"_nullFlavor":"UNK"}},"telecom":{"_nullFlavor":"UNK"}}},"participant":{"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.49"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.49"}],"text":{"reference":{"_value":"#encounterNarrative-1"}}} null AMB null 20240415063825 null HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 {"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-2"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20221213054920}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":33860921,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_roo

Section Priority Order: 2
Section being processed is: EncounterParticipant
Section Type: Struct
Section being processed: df_section_EncounterParticipant
Section Path: $.participant
Section Type: Struct
Parent section: Encounter
Parent Keys: ENCOUNTER_ID
Parent is Struct & Child is Struct:


MEDICAL_RECORD_FILENAME Document_ID ENCOUNTER_ID EncounterParticipant HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":1871606764,"_root":"F3BE3359-04CD-4C94-843D-10F0A33587CB"},"playingEntity":{"_classCode":"PLC","name":1871606764},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"i

MEDICAL_RECORD_FILENAME Document_ID ENCOUNTER_ID EncounterParticipant PARTICIPANT_TYPE_CODE PARTICIPANT_ID PARTICIPANT_CODE PARTICIPANT_CODE_SYSTEM_NAME PARTICIPANT_CODE_DISPLAY_NAME HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} null ADIR01 1160-1 HealthcareServiceLocation Urgent Care Center HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} null ADIR01 1160-1 HealthcareServiceLocation Urgent Care Center HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} null ADIR01 1160-1 HealthcareServiceLocation Urgent Care Center HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} null ADIR01 1160-1 HealthcareServiceLocation Urgent Care Center HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} null ADIR01 1160-1 HealthcareServiceLocation Urgent Care Center HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}} null ADIR01 1160-1 HealthcareServiceLocation Urgent Care Center HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 null {"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":1871606764,"_r

5. **Joining Individual sections of the entity**

In [0]:
for a in dict_level:
    print("Priority Order: ",a)
    #print(dict_section_arr[d1[a]])
    for i in [dict_level[a]]:
        print("Section being processed is:",i)

        col_list=[col['Column_Name'] for col in Columns if col['Section']==i]
        print("Columns in this section are:",col_list)
       
       
        if dict_types[i]=='Struct' :
            parentSection=dict_parent[i]
            parent_key=dict_keys[parentSection]
            
            print("Parent Keys are:",parent_key)

            key=dict_keys[i]
            if parent_key==None:
                df_parsed=df_section_elements[f'{i}']
            else:
                col_list.append(parent_key)
                
                df_parsed=df_section_elements[parentSection]
                
                df_parsed=df_parsed.join(df_section_elements[f'{i}'].select(col_list),on=parent_key,how='left')

            

display(df_parsed)

        

Priority Order:  0
Section being processed is: EncountersEntry
Columns in this section are: []
Priority Order:  1
Section being processed is: Encounter
Columns in this section are: ['ENCOUNTER_ID', 'ENCOUNTER_CODE', 'ENCOUNTER_TEXT', 'ENCOUNTER_START_TIME', 'ENCOUNTER_END_TIME']
Parent Keys are: None
Priority Order:  2
Section being processed is: EncounterParticipant
Columns in this section are: ['PARTICIPANT_TYPE_CODE', 'PARTICIPANT_ID', 'PARTICIPANT_CODE', 'PARTICIPANT_CODE_SYSTEM_NAME', 'PARTICIPANT_CODE_DISPLAY_NAME']
Parent Keys are: ENCOUNTER_ID


ENCOUNTER_ID MEDICAL_RECORD_FILENAME Document_ID Encounter ENCOUNTER_CODE ENCOUNTER_TEXT ENCOUNTER_START_TIME ENCOUNTER_END_TIME PARTICIPANT_TYPE_CODE PARTICIPANT_ID PARTICIPANT_CODE PARTICIPANT_CODE_SYSTEM_NAME PARTICIPANT_CODE_DISPLAY_NAME null HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 {"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-1"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20240415063825}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":34611941,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":12205,"state":"NY","streetAddressLine":"80 Wolf Road"},"id":[{"_root":"2.16.840.1.113883.4.319"},{"_displayable":true,"_extension":"HIXNY","_root":"2.16.840.1.113883.4.319"}],"name":"Healthcare Information Xchange of NY","telecom":{"_use":"WP","_value":"tel:(518) 640-0021"}}},"id":[{"_root":"2.16.840.1.113883.3.241.2.1"},{"_displayable":true,"_extension":"ADIR01","_root":"2.16.840.1.113883.4.319"}],"name":"Glens Falls Hospital","telecom":{"_nullFlavor":"UNK"}},"telecom":{"_nullFlavor":"UNK"}}},"participant":{"_typeCode":"LOC","participantRole":{"_classCode":"SDLOC","code":{"_code":"1160-1","_codeSystem":"2.16.840.1.113883.6.259","_codeSystemName":"HealthcareServiceLocation","_displayName":"Urgent Care Center"},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.241.2.1"},"playingEntity":{"_classCode":"PLC","name":"ADIR01"},"templateId":{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.32"}}},"templateId":[{"_root":"2.16.840.1.113883.10.20.22.4.49"},{"_extension":"2015-08-01","_root":"2.16.840.1.113883.10.20.22.4.49"}],"text":{"reference":{"_value":"#encounterNarrative-1"}}} AMB null 20240415063825 null null null null null null null HIXNY_HIXNY_37634096_017654_ADIR01_DAV_20251119170114553.xml 3b7d532f-a064-41b3-8de7-2337bf865f93 {"_classCode":"ENC","_moodCode":"EVN","code":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory","originalText":{"reference":{"_value":"#encounterDescription-2"}},"translation":{"_code":"AMB","_codeSystem":"2.16.840.1.113883.6.12","_codeSystemName":"C4","_displayName":"Ambulatory"}},"effectiveTime":{"high":{"_nullFlavor":"UNK"},"low":{"_value":20221213054920}},"id":[{"_nullFlavor":"UNK"},{"_assigningAuthorityName":"ADIR01-EncounterId","_extension":33860921,"_root":"2.16.840.1.113883.3.241.2.1"}],"informant":{"assignedEntity":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"assignedPerson":{"name":{"_nullFlavor":"UNK"}},"id":{"_extension":"ADIR01","_root":"2.16.840.1.113883.3.86.3.1"},"representedOrganization":{"addr":{"city":{"_nullFlavor":"UNK"},"country":"US","postalCode":{"_nullFlavor":"UNK"},"state":{"_nullFlavor":"UNK"},"streetAddressLine":{"_nullFlavor":"UNK"}},"asOrganizationPartOf":{"effectiveTime":{"_nullFlavor":"UNK"},"wholeOrganization":{"addr":{"_use":"WP","city":"Albany","country":"US","postalCode":1

**Writing to parsed work table**

In [0]:
%skip
tbl_name=f"T_Parsed_{compName}_{entityName}"
df_parsed.write.mode("overwrite").saveAsTable("dev_teams.racd."+tbl_name)